In [6]:
import pandas as pd
import numpy as np
from collections import Counter
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler

def balance_data_pipeline(data_path, output_path, target_col='transport_mode',
                          desired_count=50000, low_support_classes=None):
    """
    Loads data from `data_path`, applies preprocessing (e.g. merging taxi into car,
    removing low-support classes, dropping rows missing the target), then balances the
    dataset to have exactly `desired_count` samples per class using oversampling and undersampling.
    
    The balanced dataset preserves all columns for downstream tasks (e.g. LLM processing).

    Parameters:
      - data_path: Path to the original combined cleaned data CSV.
      - output_path: Path where the balanced CSV will be saved.
      - target_col: The column containing the class labels.
      - desired_count: The target number of samples per class.
      - low_support_classes: List of classes to remove (if any).
    
    Returns:
      - df_bal: The balanced DataFrame with all original features.
    """
    
    # 1. Load the data
    df = pd.read_csv(data_path)
    
    # 2. Preprocessing
    # Merge "taxi" into "car", "run" into "walk", and "subway" into "train"
    df[target_col] = df[target_col].replace({'taxi': 'car'})
    df[target_col] = df[target_col].replace({'run': 'walk'})
    df[target_col] = df[target_col].replace({'subway': 'train'})
    
    # Remove low-support classes if provided
    if low_support_classes is not None:
        df = df[~df[target_col].isin(low_support_classes)]
    
    # Drop rows missing the target column (you might add more columns here if needed)
    df = df.dropna(subset=[target_col])
    
    print("Original class distribution:")
    print(Counter(df[target_col]))
    
    # 3. Balancing the Data
    # (a) Oversample classes with fewer than desired_count samples using RandomOverSampler.
    ros_strategy = {cl: desired_count for cl, count in Counter(df[target_col]).items() if count < desired_count}
    print("\nRandomOverSampler strategy (for classes below desired count):", ros_strategy)
    
    if ros_strategy:
        ros = RandomOverSampler(sampling_strategy=ros_strategy, random_state=42)
        df_ros, y_ros = ros.fit_resample(df, df[target_col])
        # The oversampler replicates rows, so all columns are preserved.
        df = df_ros
    print("Class distribution after oversampling:")
    print(Counter(df[target_col]))
    
    # (b) Undersample classes with more than desired_count samples using RandomUnderSampler.
    rus_strategy = {cl: desired_count for cl in df[target_col].unique()}
    print("\nRandomUnderSampler strategy (forcing each class to desired count):", rus_strategy)
    
    rus = RandomUnderSampler(sampling_strategy=rus_strategy, random_state=42)
    df_bal, y_bal = rus.fit_resample(df, df[target_col])
    # Ensure the target column is set correctly
    df_bal[target_col] = y_bal
    
    print("\nFinal balanced class distribution:")
    print(Counter(df_bal[target_col]))
    
    # 4. Save the balanced DataFrame (with all original columns)
    df_bal.to_csv(output_path, index=False)
    print(f"\nBalanced data saved to {output_path}.")
    
    return df_bal

# ----- Example usage -----
data_path = "combined_cleaned_data.csv"          # Path to your original combined data
output_path = "balanced_cleaned_data.csv"         # Where the balanced data will be saved
low_support_classes = ["motorcycle", "run", "boat", "airplane"]

balanced_df = balance_data_pipeline(data_path, output_path,
                                    target_col='transport_mode',
                                    desired_count=50000,
                                    low_support_classes=low_support_classes)

Original class distribution:
Counter({'bus': 151792, 'bike': 100874, 'walk': 91292, 'train': 45572, 'car': 40012})

RandomOverSampler strategy (for classes below desired count): {'train': 50000, 'car': 50000}
Class distribution after oversampling:
Counter({'bus': 151792, 'bike': 100874, 'walk': 91292, 'train': 50000, 'car': 50000})

RandomUnderSampler strategy (forcing each class to desired count): {'train': 50000, 'walk': 50000, 'bike': 50000, 'bus': 50000, 'car': 50000}

Final balanced class distribution:
Counter({'bike': 50000, 'bus': 50000, 'car': 50000, 'train': 50000, 'walk': 50000})

Balanced data saved to balanced_cleaned_data.csv.


In [1]:
import os
import numpy as np
import pandas as pd
import geopandas as gpd
from geopy.distance import geodesic
from scipy.signal import medfilt

def calculate_time_differences_manually(df, datetime_column='datetime', output_column='time_diff'):
    """
    Calculates the time difference (in seconds) between consecutive rows.
    """
    df[datetime_column] = pd.to_datetime(df[datetime_column])
    df = df.sort_values(datetime_column).drop_duplicates(subset=[datetime_column]).reset_index(drop=True)
    datetimes = df[datetime_column].tolist()
    time_diffs = [float('nan')]
    for i in range(1, len(datetimes)):
        delta = datetimes[i] - datetimes[i-1]
        time_diffs.append(delta.total_seconds())
    df[output_column] = time_diffs
    return df

def check_raw_gps_data(df):
    """
    Prints basic diagnostics of the raw GPS data (lat/lon differences and time diff statistics).
    """
    if not pd.api.types.is_datetime64_any_dtype(df['datetime']):
        df['datetime'] = pd.to_datetime(df['datetime'])
    else:
        print("Datetime column is already in datetime64 format; proceeding as-is.")
    
    df['lat_diff'] = df['lat'].diff().abs()
    df['lon_diff'] = df['lon'].diff().abs()
    
    print("\nFirst 20 rows with differences:")
    # Assumes that calculate_time_differences_manually() has been applied
    print(df[['datetime', 'lat_diff', 'lon_diff', 'time_diff']].iloc[:20])
    print("\nTime Difference Statistics (seconds):")
    print(df['time_diff'].describe())
    
    print("\nPotential Latitude Outliers:")
    print(df[df['lat_diff'] > df['lat_diff'].mean() + 3 * df['lat_diff'].std()][['lat', 'lat_diff', 'datetime']])
    print("\nPotential Longitude Outliers:")
    print(df[df['lon_diff'] > df['lon_diff'].mean() + 3 * df['lon_diff'].std()][['lon', 'lon_diff', 'datetime']])
    print("\nPotential Time Outliers (time differences < 0.5 sec):")
    print(df[df['time_diff'] < 0.5][['datetime', 'time_diff']])
    
    return df

def clean_trajectory(df):
    """
    Performs cleaning on a raw trajectory:
      - Checks that there are enough data points
      - Computes time differences (if not already computed)
      - Computes the next coordinates, geodesic distances, and speeds
      - Applies median filtering to speed
      - Discards trajectories with unrealistic speed profiles
      - Computes bearing and bearing changes
    """
    # Discard if too few rows
    if len(df) < 10:
        print(f"Data discarded: insufficient rows ({len(df)} rows).")
        return pd.DataFrame()
    
    # Ensure time differences are available
    if 'time_diff' not in df.columns:
        df = calculate_time_differences_manually(df)
    
    # Compute next coordinates for distance and bearing calculation
    df['next_lat'] = df['lat'].shift(-1)
    df['next_lon'] = df['lon'].shift(-1)
    
    # Calculate geodesic distance (meters) between consecutive points
    df['distance'] = df.apply(
        lambda row: geodesic((row['lat'], row['lon']), (row['next_lat'], row['next_lon'])).meters
        if pd.notna(row['next_lat']) else np.nan,
        axis=1
    )
    
    # Compute speed (m/s) and smooth using median filter (kernel size=5)
    df['speed'] = df['distance'] / df['time_diff']
    df['speed'] = medfilt(df['speed'], kernel_size=5)
    
    # Basic quality control: reject trajectories with too high mean speed
    mean_speed = df['speed'].mean()
    if mean_speed > 15:
        print(f"Data discarded: mean speed too high ({mean_speed:.2f} m/s).")
        return pd.DataFrame()
    
    # Reject trajectories where more than 50% of rows have zero speed
    zero_speed_count = (df['speed'] == 0).sum()
    if zero_speed_count > len(df) * 0.5:
        print(f"Data discarded: more than 50% of rows have zero speed ({zero_speed_count} rows).")
        return pd.DataFrame()
    
    # Compute bearing between consecutive points and the absolute change in bearing
    df['bearing'] = np.where(
        pd.notna(df['next_lat']),
        compute_bearing(df['lat'], df['lon'], df['next_lat'], df['next_lon']),
        np.nan
    )
    df['bearing_change'] = df['bearing'].diff().abs().fillna(0)
    
    print(f"Data retained: {len(df)} rows after cleaning.")
    return df

# Helper: Compute bearing (used in enrichment)
def compute_bearing(lat1, lon1, lat2, lon2):
    """
    Compute bearing between two GPS coordinates.
    """
    dlon = np.radians(lon2 - lon1)
    lat1, lat2 = np.radians(lat1), np.radians(lat2)
    y = np.sin(dlon) * np.cos(lat2)
    x = np.cos(lat1) * np.sin(lat2) - np.sin(lat1) * np.cos(lat2) * np.cos(dlon)
    return np.degrees(np.arctan2(y, x)) % 360

In [2]:
from geopy.geocoders import Nominatim

def get_location_name(lat, lon):
    """
    Enriches a GPS coordinate by retrieving a human-readable location name.
    """
    geolocator = Nominatim(user_agent="geoenrichment")
    try:
        location = geolocator.reverse((lat, lon), exactly_one=True)
        return location.address
    except Exception as e:
        return "Unknown Location"

def minimal_angle_diff(diff):
    """Compute the minimal absolute difference between two angles (in degrees)."""
    diff = abs(diff) % 360
    return diff if diff <= 180 else 360 - diff

def compute_enriched_metrics(df):
    """
    Computes enriched trip metrics:
      - Step distances and overall distance (km)
      - Raw speeds with mode-based speed capping and outlier filtering
      - Acceleration (m/s²)
      - Turning metrics (bearing change, turn rate, etc.)
    """
    # Ensure time differences are available
    if 'time_diff' not in df.columns:
        df = calculate_time_differences_manually(df)
    
    # Compute next coordinates and step distance
    df['next_lat'] = df['lat'].shift(-1)
    df['next_lon'] = df['lon'].shift(-1)
    df = df.dropna(subset=['lat', 'lon', 'next_lat', 'next_lon'])
    df['step_distance'] = df.apply(
        lambda row: geodesic((row['lat'], row['lon']), (row['next_lat'], row['next_lon'])).meters,
        axis=1
    )
    total_distance = df['step_distance'].sum() / 1000  # in km
    
    # Compute raw speed (m/s)
    df['speed'] = df['step_distance'] / df['time_diff']
    
    # Apply mode-based speed cap
    if 'transport_mode' in df.columns and not df['transport_mode'].isna().all():
        mode = df['transport_mode'].mode()[0] if not df['transport_mode'].mode().empty else 'unknown'
    else:
        mode = 'unknown'
    
    speed_cap_mps = {
        'walk': 2.78,  # 10 km/h
        'bike': 6.94,  # 25 km/h
        'bus': 11.11,  # 40 km/h
        'car': 13.89,  # 50 km/h
        'taxi': 13.89, # 50 km/h
        'unknown': 13.89
    }.get(mode.lower(), 6.94)  # Default cap
    
    accel_cap_mps2 = {
        'walk': 2.0,
        'bike': 3.0,
        'bus': 3.5,
        'car': 4.0,
        'taxi': 4.0,
        'unknown': 4.0
    }.get(mode.lower(), 4.0)
    
    # Cap acceleration (if already computed) and speed
    if 'acceleration' in df.columns:
        df['acceleration'] = df['acceleration'].clip(upper=accel_cap_mps2)
    df['speed'] = df['speed'].clip(upper=speed_cap_mps)
    
    # Outlier filtering: further cap speeds based on mean + 3*std
    speed_mean = df['speed'].mean()
    speed_std = df['speed'].std()
    speed_threshold = speed_mean + 3 * speed_std
    df['speed'] = df['speed'].clip(upper=min(speed_threshold, speed_cap_mps))
    
    # Smooth speed with a median filter
    df['speed'] = medfilt(df['speed'], kernel_size=5)
    df['speed_kmh'] = df['speed'] * 3.6  # Convert m/s to km/h
    
    # Compute acceleration (m/s²)
    df['acceleration'] = df['speed'].diff() / df['time_diff']
    df['acceleration'] = df['acceleration'].fillna(0)

    # Turning metrics: Compute bearing and its change using circular difference
    df['bearing'] = df.apply(
        lambda row: compute_bearing(row['lat'], row['lon'], row['next_lat'], row['next_lon']),
        axis=1
    )

    # Use the minimal angle difference to calculate bearing changes
    df['bearing_change'] = df['bearing'].diff().apply(minimal_angle_diff)

    turn_threshold = 30  # degrees
    num_turns = (df['bearing_change'] >= turn_threshold).sum()
    duration_minutes = df['time_diff'].sum() / 60
    turn_rate = num_turns / duration_minutes if duration_minutes > 0 else 0
    avg_turn_angle = df['bearing_change'].mean()
    turn_angle_std = df['bearing_change'].std()
    
    metrics = {
        "total_distance": total_distance,
        "max_speed": df['speed_kmh'].max(),
        "min_speed": df['speed_kmh'].min(),
        "speed_std": df['speed_kmh'].std(),
        "avg_speed": df['speed_kmh'].mean(),
        "avg_acceleration": df['acceleration'].mean(),
        "max_acceleration": df['acceleration'].max(),
        "acceleration_std": df['acceleration'].std(),
        "num_turns": int(num_turns),
        "turn_rate": turn_rate,
        "avg_turn_angle": avg_turn_angle,
        "turn_angle_std": turn_angle_std,
        "avg_bearing_change": avg_turn_angle
    }
    return metrics

def generate_trip_description(df, metrics):
    """
    Generates a human-readable summary of the trip using enriched metrics.
    Also enriches the trip by retrieving start and end location names.
    """
    if df.empty:
        return "No valid data for this trip.", "Unknown"
    
    start = df.iloc[0]
    end = df.iloc[-1]
    
    start_location = get_location_name(start['lat'], start['lon'])
    end_location = get_location_name(end['lat'], end['lon'])
    
    if 'transport_mode' in df.columns and not df['transport_mode'].isna().all():
        mode_series = df['transport_mode']
        mode_value = mode_series.mode()[0]
        mode_count = (mode_series == mode_value).sum()
        total_points = len(mode_series)
        threshold = 0.6
        if (mode_count / total_points) >= threshold:
            transport_mode = mode_value
        else:
            transport_mode = "Mixed"
    else:
        transport_mode = "Unknown"
    
    description = f"""
Trip Summary:
- Start: {start['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {start_location}
- End: {end['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {end_location}
- Duration: {(end['datetime'] - start['datetime'])}
- Distance: {metrics['total_distance']:.2f} km
- Average Speed: {metrics['avg_speed']:.2f} km/h
- Average Bearing Change: {metrics['avg_bearing_change']:.2f}°
- Max Speed: {metrics['max_speed']:.2f} km/h
- Min Speed: {metrics['min_speed']:.2f} km/h
- Speed Variability: {metrics['speed_std']:.2f} km/h
- Average Acceleration: {metrics['avg_acceleration']:.2f} m/s²
- Max Acceleration: {metrics['max_acceleration']:.2f} m/s²
- Number of Turns: {metrics['num_turns']}
- Turn Rate: {metrics['turn_rate']:.2f} turns/min
- Average Turn Angle: {metrics['avg_turn_angle']:.2f}°
- Turn Angle Variability: {metrics['turn_angle_std']:.2f}°
- Transport Mode: {transport_mode}
    """
    
    # # Optionally, write the summary to a file.
    # with open("trip_summaries.txt", "a", encoding="utf-8") as f:
    #     f.write(description + "\n\n")
    
    return description, transport_mode

In [3]:
# =============================
# Step X: Generate Trip Summaries from the Balanced Dataset and Save to a File
# =============================

# Import functions from your Geolife_LLM_Pipeline notebook.
import import_ipynb
import warnings
warnings.simplefilter(action='ignore', category=pd.errors.SettingWithCopyWarning)
import os
import pandas as pd
import numpy as np

# Define the output file for trip summaries.
trip_summary_output_file = "balanced_trip_summaries.txt"

# Clear the output file before appending new summaries.
with open(trip_summary_output_file, "w", encoding="utf-8") as f:
    f.write("")

# Load the balanced dataset (ensure that the 'datetime' column is parsed as dates).
balanced_data_path = "balanced_cleaned_data.csv"
df_bal = pd.read_csv(balanced_data_path, parse_dates=['datetime'])

# Check if a trip identifier exists; if not, create one.
if 'trip_id' not in df_bal.columns:
    print("No 'trip_id' column found. Creating a dummy trip_id using grouped indices.")
    # You might choose a grouping strategy here; for demonstration, we treat each unique combination
    # of (transport_mode, date) as a trip. Adjust this logic as needed.
    df_bal['trip_id'] = df_bal.apply(lambda row: f"{row['transport_mode']}_{row['datetime'].date()}", axis=1)

# Group the DataFrame by trip_id.
trip_groups = df_bal.groupby('trip_id')

# Process each trip to generate summaries.
for trip_id, df_trip in trip_groups:
    print(f"Processing trip: {trip_id}")
    try:
        # Ensure the DataFrame has a datetime column.
        if 'datetime' not in df_trip.columns:
            print(f"Skipping {trip_id}: Missing 'datetime' column.")
            continue

        # Calculate time differences (if not already computed).
        df_trip = calculate_time_differences_manually(df_trip)

        # If the trip has fewer than 2 data points, skip summary generation.
        if len(df_trip) < 2:
            print(f"Skipping {trip_id}: Not enough points for a trip summary.")
            continue

        # Compute enriched metrics from the subtrajectory.
        metrics = compute_enriched_metrics(df_trip)

        # Generate a trip summary using your predefined function.
        # generate_trip_description returns (description, transport_mode)
        trip_summary, transport_mode = generate_trip_description(df_trip, metrics)
        print(trip_summary)

        # Append the trip summary to the output file.
        with open(trip_summary_output_file, "a", encoding="utf-8") as f:
            f.write(trip_summary + "\n\n")
    
    except Exception as e:
        print(f"Error processing trip {trip_id}: {e}")

print("Trip summary generation complete.")

No 'trip_id' column found. Creating a dummy trip_id using grouped indices.
Processing trip: bike_2007-10-06


/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['step_distance'] = df.apply(
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['speed'] = df['step_distance'] / df['time_diff']
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr


Trip Summary:
- Start: 2007-10-06 09:23:27 at 小翔凤胡同, 什刹海, 什刹海街道, 首都功能核心区, 西城区, 北京市, 100032, 中国
- End: 2007-10-06 09:34:23 at 毡子胡同, 什刹海, 什刹海街道, 首都功能核心区, 西城区, 北京市, 100032, 中国
- Duration: 0 days 00:10:56
- Distance: 0.49 km
- Average Speed: 2.88 km/h
- Average Bearing Change: 91.66°
- Max Speed: 7.11 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 2.47 km/h
- Average Acceleration: -0.03 m/s²
- Max Acceleration: 0.02 m/s²
- Number of Turns: 5
- Turn Rate: 0.46 turns/min
- Average Turn Angle: 91.66°
- Turn Angle Variability: 61.67°
- Transport Mode: bike
    
Processing trip: bike_2008-03-10


/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['step_distance'] = df.apply(
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['speed'] = df['step_distance'] / df['time_diff']
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr


Trip Summary:
- Start: 2008-03-10 17:12:18 at 中关村东路, 知春东里社区, 中关村街道, 海淀区, 北京市, 100190, 中国
- End: 2008-03-10 17:26:46 at 清华大学, 30, 双清路, 东升镇, 海淀区, 北京市, 100084, 中国
- Duration: 0 days 00:14:28
- Distance: 3.16 km
- Average Speed: 11.43 km/h
- Average Bearing Change: 12.06°
- Max Speed: 24.98 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 7.48 km/h
- Average Acceleration: 0.02 m/s²
- Max Acceleration: 0.13 m/s²
- Number of Turns: 1
- Turn Rate: 0.10 turns/min
- Average Turn Angle: 12.06°
- Turn Angle Variability: 16.04°
- Transport Mode: bike
    
Processing trip: bike_2008-03-11


...

/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['step_distance'] = df.apply(
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['speed'] = df['step_distance'] / df['time_diff']
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr


Trip Summary:
- Start: 2011-10-21 14:41:48 at Unknown Location
- End: 2011-10-21 14:47:43 at Unknown Location
- Duration: 0 days 00:05:55
- Distance: 0.56 km
- Average Speed: 4.36 km/h
- Average Bearing Change: 33.08°
- Max Speed: 9.95 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 1.94 km/h
- Average Acceleration: 0.01 m/s²
- Max Acceleration: 0.33 m/s²
- Number of Turns: 12
- Turn Rate: 2.06 turns/min
- Average Turn Angle: 33.08°
- Turn Angle Variability: 36.86°
- Transport Mode: walk
    
Processing trip: walk_2011-10-22

Trip Summary:
- Start: 2011-10-22 10:02:41 at Unknown Location
- End: 2011-10-22 10:03:21 at Unknown Location
- Duration: 0 days 00:00:40
- Distance: 0.02 km
- Average Speed: 2.61 km/h
- Average Bearing Change: 65.21°
- Max Speed: 10.01 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 4.93 km/h
- Average Acceleration: 0.30 m/s²
- Max Acceleration: 1.36 m/s²
- Number of Turns: 3
- Turn Rate: 5.45 turns/min
- Average Turn Angle: 65.21°
- Turn Angle Variability: 41

/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['step_distance'] = df.apply(
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['speed'] = df['step_distance'] / df['time_diff']
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr


Trip Summary:
- Start: 2011-11-09 11:15:47 at Unknown Location
- End: 2011-11-09 11:24:57 at Unknown Location
- Duration: 0 days 00:09:10
- Distance: 1.08 km
- Average Speed: 5.96 km/h
- Average Bearing Change: 70.98°
- Max Speed: 10.01 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 2.81 km/h
- Average Acceleration: -0.01 m/s²
- Max Acceleration: 0.36 m/s²
- Number of Turns: 47
- Turn Rate: 5.17 turns/min
- Average Turn Angle: 70.98°
- Turn Angle Variability: 55.37°
- Transport Mode: walk
    
Processing trip: walk_2011-11-12

Trip Summary:
- Start: 2011-11-12 12:47:40 at Unknown Location
- End: 2011-11-12 12:49:15 at Unknown Location
- Duration: 0 days 00:01:35
- Distance: 0.15 km
- Average Speed: 4.35 km/h
- Average Bearing Change: 33.95°
- Max Speed: 10.01 km/h
- Min Speed: 0.00 km/h
- Speed Variability: 2.71 km/h
- Average Acceleration: 0.02 m/s²
- Max Acceleration: 0.49 m/s²
- Number of Turns: 6
- Turn Rate: 4.00 turns/min
- Average Turn Angle: 33.95°
- Turn Angle Variability: 

/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['step_distance'] = df.apply(
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['speed'] = df['step_distance'] / df['time_diff']
/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_41191/3283016476.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr